In [1]:
import numpy as np
import pandas as pd
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as plt
%matplotlib inline

In [3]:
# Read the .csv file
fine_food_reviews = pd.read_csv('data/Amazon-fine-food-reviews.csv')

### Goal of the project is to predict fine-food scores for the Amazon dataset using a user-based collaborative filtering technique.

### Part 1 consists of the following:
### (i) Data Processing and Cleaning   (ii) Exploratory Data Analysis

## Data processing and cleaning

In [4]:
# Check the first 5 rows of the dataset
# .head() method will display the first 5 rows of the dataframe by default
fine_food_reviews.head()

Id   ProductId          UserId                      ProfileName  \
0   1  B001E4KFG0  A3SGXH7AUHU8GW                       delmartian   
1   2  B00813GRG4  A1D87F6ZCVE5NK                           dll pa   
2   3  B000LQOCH0   ABXLMWJIXXAIN  Natalia Corres "Natalia Corres"   
3   4  B000UA0QIQ  A395BORC6FGVXV                             Karl   
4   5  B006K2ZZ7K  A1UQRSCLF8GW1T    Michael D. Bigham "M. Wassir"   

   HelpfulnessNumerator  HelpfulnessDenominator  Score        Time  \
0                     1                       1      5  1303862400   
1                     0                       0      1  1346976000   
2                     1                       1      4  1219017600   
3                     3                       3      2  1307923200   
4                     0                       0      5  1350777600   

                 Summary                                               Text  
0  Good Quality Dog Food  I have bought several of the Vitality canned d...  
1      Not as Advertised  Product arrived labeled as Jumbo Salted Peanut...  
2  "Delight" says it all  This is a confection that has been around a fe...  
3         Cough Medicine  If you are looking for the secret ingredient i...  
4            Great taffy  Great taffy at a great price.  There was a wid...

In [5]:
# Check for the number of rows and columns in the dataset
fine_food_reviews.shape

(568454, 10)

- There are 568,454 rows and 10 columns in the dataset

In [6]:
# Summary statistics is only provided only for the HelpfulnessNumerator, HelpfulnessDenominator, and Score columns
fine_food_reviews[['HelpfulnessNumerator','HelpfulnessDenominator','Score']].describe()

HelpfulnessNumerator  HelpfulnessDenominator          Score
count         568454.000000            568454.00000  568454.000000
mean               1.743817                 2.22881       4.183199
std                7.636513                 8.28974       1.310436
min                0.000000                 0.00000       1.000000
25%                0.000000                 0.00000       4.000000
50%                0.000000                 1.00000       5.000000
75%                2.000000                 2.00000       5.000000
max              866.000000               923.00000       5.000000

In [7]:
# Display the information on the different columns in the dataframe including number of null values and data types
fine_food_reviews.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 568454 entries, 0 to 568453
Data columns (total 10 columns):
Id                        568454 non-null int64
ProductId                 568454 non-null object
UserId                    568454 non-null object
ProfileName               568438 non-null object
HelpfulnessNumerator      568454 non-null int64
HelpfulnessDenominator    568454 non-null int64
Score                     568454 non-null int64
Time                      568454 non-null int64
Summary                   568427 non-null object
Text                      568454 non-null object
dtypes: int64(5), object(5)
memory usage: 43.4+ MB


In [8]:
# Show the total number of null values for each column
fine_food_reviews.isna().sum()

Id                         0
ProductId                  0
UserId                     0
ProfileName               16
HelpfulnessNumerator       0
HelpfulnessDenominator     0
Score                      0
Time                       0
Summary                   27
Text                       0
dtype: int64

- The **`ProfileName`** and **`Summary`** columns both have null values. The purpose of this project is to predict user scores so all rows from the with no **`Summary`** will be removed.

In [9]:
# Create a copy of the dataframe
new_reviews=fine_food_reviews.copy()

In [10]:
# Remove all rows in the dataset with no summary provided
new_reviews=fine_food_reviews.dropna(subset=['Summary'])

In [11]:
# Check for the number of rows and columns in the dataset
new_reviews.shape

(568427, 10)

In [12]:
# Check to make sure that all rows with no summary have been removed from the dataset
new_reviews.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 568427 entries, 0 to 568453
Data columns (total 10 columns):
Id                        568427 non-null int64
ProductId                 568427 non-null object
UserId                    568427 non-null object
ProfileName               568411 non-null object
HelpfulnessNumerator      568427 non-null int64
HelpfulnessDenominator    568427 non-null int64
Score                     568427 non-null int64
Time                      568427 non-null int64
Summary                   568427 non-null object
Text                      568427 non-null object
dtypes: int64(5), object(5)
memory usage: 47.7+ MB


- All rows with no **`summary`** have been removed from the dataset

- There are 16 missing names from the dataset. Rather than dropping the rows, I will fill with the same string value since the 
primary goal of this project is to predict user scores for different products.

In [13]:
#Replace all null values in the ProfileName with the name 'Team Scientist'
new_reviews['ProfileName'].fillna('Team Scientist', inplace=True)

C:\Users\LuisV\Anaconda3\lib\site-packages\pandas\core\generic.py:6287: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [14]:
# Find the total sum of null values for all columns again
new_reviews.isna().sum()

Id                        0
ProductId                 0
UserId                    0
ProfileName               0
HelpfulnessNumerator      0
HelpfulnessDenominator    0
Score                     0
Time                      0
Summary                   0
Text                      0
dtype: int64

- There no null values left in the dataset!

In [15]:
# Check for any duplicate rows in the dataset. If any,keep the first row of the the duplicates.
result_df = new_reviews.drop_duplicates()

- There are no duplicate rows in the dataset

In [16]:
# Find the number of rows and columns in the dataframe
result_df.shape

(568427, 10)

## Exploratory Data Analysis

- Find the minimum and maximum score a user can provide for a product

In [17]:
# Maximum score a user can provide for a product
result_df['Score'].max()

5

In [18]:
# Minimum score for a product that can be assigned by a user
result_df['Score'].min()

1

In [19]:
# Perform the following operations:
# Retrieve the Score column of the dataframe. Find the total of each Score category. 
# Save the result in a new dataframe and reset the index of the dataframe.

score=pd.DataFrame(result_df['Score'].value_counts().sort_values().reset_index())

In [20]:
# Check the dataframe
score

index   Score
0      2   29744
1      3   42638
2      1   52268
3      4   80655
4      5  363122

In [21]:
# Rename columns of the dataframe
score.columns=['Score','Total_for_score_category']

In [22]:
# Check to make sure that the column names have changed
score.head()

Score  Total_for_score_category
0      2                     29744
1      3                     42638
2      1                     52268
3      4                     80655
4      5                    363122

In [24]:
# Plot a bar graph to inspect the distribution of scores

fig = px.bar(score, x="Score",y='Total_for_score_category',width=600,height=600)
fig.update_layout(xaxis_showgrid=False, yaxis_showgrid=False)
fig.update_layout(title_text='The most common score given by a user is 5')
fig.update_traces(marker_color='blue')
fig.show()

In [25]:
# Find the number of unique products
result_df['ProductId'].nunique()

74258

In [26]:
# Find the number of unique users
result_df['UserId'].nunique()

256056

- There are 74,258 unique products and 256,056 distinct users.

In [27]:
# Create a new dataframe with the number of times different products have been assigned a score
# Also, rename the columns of the dataframe
products=pd.DataFrame(result_df['ProductId'].value_counts().sort_values().reset_index())

In [28]:
# Rename the columns of the dataframe
products.columns=['ProductId','Num_of_Scores']

In [29]:
# Check the first 3 rows of the dataframe
products.head(3)

ProductId  Num_of_Scores
0  B004GFSRTQ              1
1  B000NX3E2K              1
2  B000KHU5US              1

In [30]:
products.shape

(74258, 2)

In [31]:
# Plot a histogram that shows the distribution of scores for all products
fig = px.histogram(products,x='Num_of_Scores', nbins=80,log_y =True)
fig.update_layout(xaxis_showgrid=False, yaxis_showgrid=False)
fig.update_layout(title_text='Over 69,000 products have a been asssigned a score less than 20 times')
fig.update_traces(marker_color='blue')
fig.show()

In [32]:
# Find the number of times each user has provided a score for a product
userID=pd.DataFrame(result_df['UserId'].value_counts().sort_values(ascending=True).reset_index())

In [33]:
# Display the first few rows of the dataframe
userID.head()

index  UserId
0   A5WHOQ7PPXDBE       1
1  A1NPSGATHDT0CO       1
2  A2FENVB93A9FNW       1
3  A3MV6SD9TXO1X7       1
4  A15K6MCI813OFQ       1

In [34]:
# Change the column names
userID.columns=['UserId','Num_of_scores_assigned']

In [35]:
# Check to ensure that column names have been changed
userID.head()

UserId  Num_of_scores_assigned
0   A5WHOQ7PPXDBE                       1
1  A1NPSGATHDT0CO                       1
2  A2FENVB93A9FNW                       1
3  A3MV6SD9TXO1X7                       1
4  A15K6MCI813OFQ                       1

In [36]:
# Check the number of rows and columns
userID.shape

(256056, 2)

In [37]:
# Plot a histogram that shows the distribution of scores for all users
fig = px.histogram(userID,x='Num_of_scores_assigned',log_y=True, nbins=50)
fig.update_layout(xaxis_showgrid=False, yaxis_showgrid=False)
fig.update_layout(title_text='Over 247000 customers have assigned a score for less than 10 different products')
fig.update_traces(marker_color='blue')
fig.show()

- Customers generally do not provide ratings for different products.There are 256056 unique User Id's and over 247000 have provided scores for less than 10 different products. 

# Part 2: Modeling

- In order to avoid running into memory error, User Id's that have assigned a score to less than 10 products will be filtered out.

In [37]:
# Create a subset of the userID dataframe that contains only user Id's that have provided a score for more than 10 products.
new_df= userID[userID['Num_of_scores_assigned']>10]

In [38]:
 # Check the number of rows and columns in the dataframe
new_df.shape

(6358, 2)

In [39]:
# Default merge (inner merge) to only keep rows with ProductID's that exists in both left and right dataframes
model_df = pd.merge(result_df,new_df,on='UserId')

In [40]:
# Check the first 3 rows of the merged dataframe
model_df.head(3)

Id   ProductId          UserId             ProfileName  \
0      12  B0009XLVG0  A2725IB4YY9JEB  A Poeng "SparkyGoHome"   
1    3938  B001L1KH6Y  A2725IB4YY9JEB  A Poeng "SparkyGoHome"   
2  135729  B003THML30  A2725IB4YY9JEB  A Poeng "SparkyGoHome"   

   HelpfulnessNumerator  HelpfulnessDenominator  Score        Time  \
0                     4                       4      5  1282867200   
1                     3                       3      5  1232323200   
2                     0                       0      5  1285718400   

                                             Summary  \
0  My cats LOVE this "diet" food better than thei...   
1  LOVE this coffee.  Packs a wallop in the morning.   
2                               Awesomely delicious!   

                                                Text  Num_of_scores_assigned  
0  One of my boys needed to lose some weight and ...                      12  
1  If I drank more than one commuter cup in the m...                      12  
2  Love Cliff bars, but have only liked the Peanu...                      12

In [41]:
# Check the number of rows and columns in the dataframe
model_df.shape

(128959, 11)

In [42]:
# Import the following modules from the Surprise 
from surprise import SVD
from surprise import SVDpp
from surprise import SlopeOne
from surprise import NMF
from surprise import NormalPredictor
from surprise import KNNBaseline
from surprise import KNNBasic
from surprise import KNNWithMeans
from surprise import BaselineOnly
from surprise import CoClustering
from surprise import Dataset
from surprise.model_selection import cross_validate
from surprise.model_selection import GridSearchCV
from surprise import Reader

In [43]:
# Rating scale to be used as part of the process of using Surprise to predict ratings ("Scores" in this case)
reader = Reader(rating_scale=(1, 5))

# Convert the pandas dataframe into a Surprise dataset using the load_from_df() method
# The 'UserId', 'ProductId', and ratings ('Score' in this case) are passed in the exact order
data = Dataset.load_from_df(model_df[['UserId', 'ProductId', 'Score']], reader)

In [44]:
# Create an empty list
algorithm_result = []

# Iterate over all algorithms
for algorithm in [SVD(), SVDpp(), SlopeOne(), NMF(), NormalPredictor(), KNNBaseline(), KNNBasic(), KNNWithMeans(), BaselineOnly(), CoClustering()]:
    # Perform cross validation
    results = cross_validate(algorithm, data, measures=['RMSE'], cv=3, verbose=False)
    
    # Get results & append algorithm name
    tmp = pd.DataFrame.from_dict(results).mean(axis=0)
    tmp = tmp.append(pd.Series([str(algorithm).split(' ')[0].split('.')[-1]], index=['Algorithm']))
    algorithm_result.append(tmp)

Estimating biases using als...
Computing the msd similarity matrix...
Done computing similarity matrix.
Estimating biases using als...
Computing the msd similarity matrix...
Done computing similarity matrix.
Estimating biases using als...
Computing the msd similarity matrix...
Done computing similarity matrix.
Computing the msd similarity matrix...
Done computing similarity matrix.
Computing the msd similarity matrix...
Done computing similarity matrix.
Computing the msd similarity matrix...
Done computing similarity matrix.
Computing the msd similarity matrix...
Done computing similarity matrix.
Computing the msd similarity matrix...
Done computing similarity matrix.
Computing the msd similarity matrix...
Done computing similarity matrix.
Estimating biases using als...
Estimating biases using als...
Estimating biases using als...


In [45]:
# Create a datframe with results of the grid search
pd.DataFrame(algorithm_result).set_index('Algorithm').sort_values('test_rmse') 

test_rmse   fit_time  test_time
Algorithm                                       
KNNBaseline       0.852116   2.391283   5.827705
SVDpp             0.856090  36.584486   2.313632
SVD               0.885788   6.041125   0.389352
KNNWithMeans      0.894681   2.073705   5.066487
KNNBasic          0.926278   1.904513   4.507350
SlopeOne          0.948139  32.282162   1.782447
CoClustering      0.965559   5.869807   0.471870
NMF               0.980699  10.614850   0.464694
BaselineOnly      0.983810   0.473713   0.616273
NormalPredictor   1.558011   0.204238   0.500311

- `KNNBaseline` had the lowest RMSE in the gridsearch and is the algorithm that will be fitted to the data in order to eventually predict ratings.

In [48]:
print('Using SGD')
bsl_options= { 'method': 'sgd',
               'learning_rate':.00005              
             }

# 'user_based' in the similarity option (sim_options) is set to True in order to compute a User based collaborative filtering.
sim_options= {'name':'pearson_baseline', 
              'user_based':True
             } 

algo = KNNBaseline(bsl_options=bsl_options,sim_options=sim_options)

cross_validate(algo, data, measures=['RMSE'], cv=3, verbose=False)

Using SGD
Estimating biases using sgd...
Computing the pearson_baseline similarity matrix...
Done computing similarity matrix.
Estimating biases using sgd...
Computing the pearson_baseline similarity matrix...
Done computing similarity matrix.
Estimating biases using sgd...
Computing the pearson_baseline similarity matrix...
Done computing similarity matrix.


{'test_rmse': array([0.97630608, 0.97400572, 0.98279438]),
 'fit_time': (4.83288049697876, 4.470227003097534, 4.589086294174194),
 'test_time': (5.271914482116699, 5.2202935218811035, 4.822697162628174)}

 - The next step in this process is to split the data into the train and test...

In [49]:
from surprise.model_selection import train_test_split
from surprise import accuracy

# split the data into train and test set
# Use 75% of the dataset for training and 25% for testing
trainset, testset = train_test_split(data, test_size=0.25)

# Instantiate the KNNBaseline Algorithm
algo = KNNBaseline(bsl_options=bsl_options, sim_options=sim_options)

# Fit algorithm to the training set
algo.fit(trainset)

# Predict ratings for the test set
test_set_predictions=algo.test(testset)

# Calculate the root mean squared error(RMSE)
accuracy.rmse(test_set_predictions)

Estimating biases using sgd...
Computing the pearson_baseline similarity matrix...
Done computing similarity matrix.
RMSE: 0.9608


0.9607705052931593

- Source of code to build a pandas dataframe with the predictions is given below:
- [Predictions dataframe](https://towardsdatascience.com/building-and-testing-recommender-systems-with-surprise-step-by-step-d4ba702ef80b)

In [ ]:
# Let's build a pandas dataframe with all the predictions

def get_Iu(uid):
    """Return the number of items rated by given user
    
    Args:
        uid: The raw id of the user.
    Returns:
        The number of items rated by the user.
    """
    
    try:
        return len(trainset.ur[trainset.to_inner_uid(uid)])
    except ValueError:  # user was not part of the trainset
        return 0
    
def get_Ui(iid):
    """Return the number of users that have rated given item
    
    Args:
        iid: The raw id of the item.
    Returns:
        The number of users that have rated the item.
    """
    
    try:
        return len(trainset.ir[trainset.to_inner_iid(iid)])
    except ValueError:  # item was not part of the trainset
        return 0

# Create a dataframe with the test_set predictions    
df = pd.DataFrame(test_set_predictions, columns=['uid', 'iid', 'rui', 'est', 'details'])    
df['Iu'] = df.uid.apply(get_Iu)
df['Ui'] = df.iid.apply(get_Ui)
df['err'] = abs(df.est - df.rui)

In [70]:
# Create a subset of the dataframe with the top 10 best predictions
best_predictions = df.sort_values(by='err')[:10]

# Create a subset of the dataframe with the top 10 worst predictions
worst_predictions = df.sort_values(by='err')[-10:]

### Key for the tables below is provided as follows with column names(from left to right):


- **`uid`** - user Id
- **`iid`** - product Id
- **`rui`** - the estimated rating of user u for item i.
- **`est`** - prediction by the KNNBaseline algorithm
- **`details`** - dictionary of prediction with `actual_k` field (number of nearest neigbors used in score prediction)
- **`Iu`** - the set of all items rated by user u.
- **`Ui`** - the set of all users that have rated item i.
- **`err`** - absolute value of the difference between **`est`** and **`rui`**


In [51]:
# The top 10 predictions in the dataframe based on smallest error value
best_predictions

uid         iid  rui  est  \
16468  A1YDQ8I5KVNF8P  B002T0IHPO  5.0  5.0   
16242  A2LIF95N23RT72  B0029XLH4Y  5.0  5.0   
26226  A250AXLRBVYKB4  B001SIY414  5.0  5.0   
11146  A3AZI828WJN1CD  B005ZBZLPI  5.0  5.0   
16260  A2PF32UUERJXB8  B000FBO9MO  5.0  5.0   
4156   A1HM9ZCU43N6XD  B001CU0N4A  5.0  5.0   
26189   AZA595ZPIG240  B005QRPH3M  5.0  5.0   
4169   A2M9OWAU1VQ0VT  B0014AUJII  5.0  5.0   
4185   A3DOPYDOS49I3T  B0007A0AQW  5.0  5.0   
26162  A29JUMRL1US6YP  B0002Z9BF8  5.0  5.0   

                                         details   Iu   Ui  err  
16468  {'actual_k': 31, 'was_impossible': False}   15   87  0.0  
16242  {'actual_k': 10, 'was_impossible': False}   18   33  0.0  
26226  {'actual_k': 34, 'was_impossible': False}   88   73  0.0  
11146   {'actual_k': 1, 'was_impossible': False}   49    5  0.0  
16260  {'actual_k': 37, 'was_impossible': False}   25   45  0.0  
4156    {'actual_k': 2, 'was_impossible': False}   17   10  0.0  
26189  {'actual_k': 13, 'was_impossible': False}   16   29  0.0  
4169   {'actual_k': 40, 'was_impossible': False}   22  122  0.0  
4185   {'actual_k': 40, 'was_impossible': False}   42   63  0.0  
26162   {'actual_k': 1, 'was_impossible': False}  133    1  0.0

- All products in the table for the top 10 best predictions have been rated by many users with the exception of three from 
(row numbers `11146`,`26162`,and `4156`). These are suspect and might have been lucky shots because only a few customers provided scores for the corresponding product (**`Ui`**). The number of neighbors used to predict the scores (i.e. `actual_k`) for these products is very low. 

- It therefore seems to be a coincidence that these products rated by few customers have scores equal to that of the target user.

In [52]:
# Show the top 10 worst predictions based on error value
worst_predictions

uid         iid  rui       est  \
6555    ATUNQTRTF2285  B001EO5Y52  5.0  1.005257   
25765  A2K89R0B20LYHB  B004X8TG3M  1.0  4.995616   
21526   AAKOCT2HJRWW0  B002ANCCK6  1.0  4.997440   
23620  A2MUGFV2TDQ47K  B002BC1YFK  5.0  1.000000   
15400   AAEGIBOD9UGOL  B004XAPIOQ  1.0  5.000000   
7969   A11SXJ2H7IC8J7  B005YYFHCS  5.0  1.000000   
8491   A1IH42TUIZ2XJL  B002AQ0OL2  5.0  1.000000   
17505   AKRZSLATNVUH6  B0044BSZL2  5.0  1.000000   
22877  A2FRFAQCWZJT3Q  B001BOVE54  1.0  5.000000   
20375  A35JP8KSV9281K  B001E52VR0  1.0  5.000000   

                                        details   Iu  Ui       err  
6555   {'actual_k': 1, 'was_impossible': False}    4   4  3.994743  
25765  {'actual_k': 1, 'was_impossible': False}   33   4  3.995616  
21526  {'actual_k': 1, 'was_impossible': False}    8   4  3.997440  
23620  {'actual_k': 1, 'was_impossible': False}  156   1  4.000000  
15400  {'actual_k': 1, 'was_impossible': False}   12   7  4.000000  
7969   {'actual_k': 1, 'was_impossible': False}   12   4  4.000000  
8491   {'actual_k': 1, 'was_impossible': False}   40  10  4.000000  
17505  {'actual_k': 1, 'was_impossible': False}    9   1  4.000000  
22877  {'actual_k': 2, 'was_impossible': False}  126   8  4.000000  
20375  {'actual_k': 1, 'was_impossible': False}   61   1  4.000000

- All products in the top 10 worst predictions seemed to have been rated by few customers and all (except for 1 case) had a score prediction based on 1 nearest neighbor. Increasing the minimum number of neighbors (**`min_k`**) would help avoid these errors in prediction. A higher **`min_k`** value increases the number of neighbors taken into account for aggregation, which in turn reduces accuracy for the model. This is because a mean of the value is used for prediction if the number of neighbors is below the threshold of **`min_k`**.
